Preprocesses e621's [data exports](https://e621.net/db_export/) and stores them in feather files. The feather format was chosen because it loads quickly!

Usage notes:
* Feel free to change `INPUT_FOLDER` and `OUTPUT_FOLDER` to anywhere you want to store your data.
* `DATE` is whatever date is on your input files.
* Files will only be generated if they don't already exist. Delete them if you want to regenerate.

In [ ]:
import pandas
import os
from tqdm.notebook import tqdm
tqdm.pandas()

INPUT_FOLDER = "H:/Data/TagSuggest/e621_metadata"
OUTPUT_FOLDER = "H:/Data/TagSuggest/e621_dataframes"
DATE = "2023-08-23"

os.makedirs(OUTPUT_FOLDER, exist_ok=True)

The first thing to process is the tags themselves, since we'll be using their IDs
* `tag_id` - An arbitrary number from e621's database. Very useful.
* `name` - The tag!
* `category` - A number to say whether it's an artist, species, and so on. Constants for these are defined elsewhere, this notebook doesn't need to know them.
* `post_count` - The approximate number of posts the tag has. It's not perfectly aligned with the actual post data, but it's close enough for most purposes.

In [ ]:
tags_file = f"{OUTPUT_FOLDER}/tags.feather"
if os.path.exists(tags_file):
    tags = pandas.read_feather(tags_file)
else:
    tags = pandas.read_csv(f"{INPUT_FOLDER}/tags-{DATE}.csv.gz", na_values=[], keep_default_na=False).astype({"name":"string"}).rename(columns={"id": "tag_id"}).reset_index(drop=True)
    tags.to_feather(tags_file)
tags.info()

In [ ]:
tags_by_name = tags.copy(deep=True)
tags_by_name.set_index("name", inplace=True)
tags_by_name.info()

This part takes a couple minutes! There are about 4 million posts to go through, and each one has the tags listed in string format, so they have to be parsed and translated to IDs for more compact storage. The progress bar is based on exactly four million posts, which is low now, but it's not worth actually counting the lines. Two dataframes are generated:

* The posts file contains most of the post data.
    * `post_id` - From e621. Used for linking to the other dataframe.
    * `rating` - Whether the post is safe, questionable, or explicit. Handy if you want to generate SFW wildcards.
    * `score` - The overall user score of the post, if you're curious. Score doesn't necessarily correlate to aesthetic quality; posts can be highly upvoted because of their content or themes irrespective of their art style.
    * `up_score` - The upvote component of the score. Just guessing, but people probably upvote and downvote for totally different reasons, so it could be useful.
    * `down_score` - The downvote component of the score as a negative. If it's big, it's probably an unpopular niche kink or a political meme or something.
* The post tags file stores the links between posts and tags as numbers. It's surprisingly large.

In [ ]:
post_tags_file = f"{OUTPUT_FOLDER}/post_tags.feather"
posts_file = f"{OUTPUT_FOLDER}/posts.feather"
if os.path.exists(post_tags_file) and os.path.exists(posts_file):
    post_tags = pandas.read_feather(post_tags_file)
    posts = pandas.read_feather(posts_file)
else:
    post_tags_parts = []
    posts_parts = []
    with pandas.read_csv(f"{INPUT_FOLDER}/posts-{DATE}.csv.gz", usecols=["id", "tag_string", "is_deleted", "is_pending", "rating", "score", "up_score", "down_score"], chunksize=100_000) as reader:
        progress = tqdm(total=4_000_000)
        for posts in reader:
            post_count = len(posts)
            posts: pandas.DataFrame
            posts = posts[posts["is_deleted"] == "f"]
            posts = posts[posts["is_pending"] == "f"]
            posts = posts.rename(columns={"id": "post_id"})
            posts_parts.append(posts[["post_id", "rating", "score", "up_score", "down_score"]].astype({"rating":"string"}))
            posts = posts[["post_id", "tag_string"]].set_index("post_id")
            posts = posts.apply(lambda x: x.str.split(' ')).explode("tag_string")
            posts = posts.join(tags_by_name, on="tag_string")[["tag_id"]].reset_index()
            post_tags_parts.append(posts[["post_id", "tag_id"]])
            progress.update(post_count)
    post_tags = pandas.concat(post_tags_parts)
    post_tags.reset_index(drop=True, inplace=True)
    post_tags.to_feather(post_tags_file)
    posts = pandas.concat(posts_parts)
    posts.reset_index(drop=True, inplace=True)
    posts.to_feather(posts_file)
print("\npost_tags")
post_tags.info()
print("\nposts")
posts.info()

We also generate and store two different ways of looking at the `post_tags` frame, because it's a lot faster to cache this once than to join a many-to-many frame that size for every single query. This can also take a few minutes.

In [ ]:

posts_by_tag_file = f"{OUTPUT_FOLDER}/posts_by_tag.feather"
if os.path.exists(posts_by_tag_file):
    posts_by_tag = pandas.read_feather(posts_by_tag_file)
else:
    posts_by_tag = post_tags.groupby("tag_id").progress_aggregate(list)
    posts_by_tag.reset_index(inplace=True)
    posts_by_tag.to_feather(posts_by_tag_file)
posts_by_tag.info()

In [ ]:
tags_by_post_file = f"{OUTPUT_FOLDER}/tags_by_post.feather"
if os.path.exists(tags_by_post_file):
    tags_by_post = pandas.read_feather(tags_by_post_file)
else:
    tags_by_post = post_tags.groupby("post_id").progress_aggregate(list)
    tags_by_post.reset_index(inplace=True)
    tags_by_post.to_feather(tags_by_post_file)
tags_by_post.info()

Also make a SFW post tags list, then use it to build a list of tags that only appear in SFW posts. Optional.

In [ ]:
safe_posts_by_tag_file = f"{OUTPUT_FOLDER}/safe_posts_by_tag.feather"
if os.path.exists(safe_posts_by_tag_file):
    safe_posts_by_tag = pandas.read_feather(safe_posts_by_tag_file)
else:
    safe_posts_by_tag = post_tags.set_index("post_id").join(posts.set_index("post_id"))
    safe_posts_by_tag = safe_posts_by_tag[safe_posts_by_tag["rating"].isin(["s"])].reset_index()
    safe_posts_by_tag = safe_posts_by_tag[["tag_id", "post_id"]].groupby("tag_id").progress_aggregate(list)
    safe_posts_by_tag.reset_index(inplace=True)
    safe_posts_by_tag.to_feather(safe_posts_by_tag_file)
safe_posts_by_tag.info()

In [ ]:
safe_tags_by_post_file = f"{OUTPUT_FOLDER}/safe_tags_by_post.feather"
if os.path.exists(safe_tags_by_post_file):
    safe_tags_by_post = pandas.read_feather(safe_tags_by_post_file)
else:
    safe_tags_by_post = post_tags.set_index("post_id").join(posts.set_index("post_id"))
    safe_tags_by_post = safe_tags_by_post[safe_tags_by_post["rating"].isin(["s"])].reset_index()
    safe_tags_by_post = safe_tags_by_post[["tag_id", "post_id"]].groupby("post_id").progress_aggregate(list)
    safe_tags_by_post.reset_index(inplace=True)
    safe_tags_by_post.to_feather(safe_tags_by_post_file)
safe_tags_by_post.info()

In [ ]:
safe_tags_file = f"{OUTPUT_FOLDER}/safe_tags.feather"
if os.path.exists(safe_tags_file):
    safe_tags = pandas.read_feather(safe_tags_file)
else:
    safe_tags = safe_posts_by_tag.set_index("tag_id").join(tags.set_index("tag_id"), how="inner")
    safe_tags["post_count"] = safe_tags["post_id"].apply(len)
    safe_tags = safe_tags[["name", "category", "post_count"]]
    safe_tags.reset_index(inplace=True)
    safe_tags.to_feather(safe_tags_file)
safe_tags.info()

And lastly, parse and store the implications file. Useful for filtering out tag suggestions that are implied by higher scoring ones, and for building the species hierarchy.

In [ ]:
implications_file = f"{OUTPUT_FOLDER}/implications.feather"
if os.path.exists(implications_file):
    implications = pandas.read_feather(implications_file)
else:
    implications = pandas.read_csv(f"{INPUT_FOLDER}/tag_implications-{DATE}.csv.gz")\
        .join(tags_by_name, on="antecedent_name", how="inner")\
        .join(tags_by_name, on="consequent_name", rsuffix="_con")\
        [["tag_id", "tag_id_con"]]\
        .rename(columns={"tag_id": "antecedent_id", "tag_id_con": "consequent_id"})
    implications.reset_index(inplace=True,drop=True)
    implications.to_feather(implications_file)
implications.info()